In [1]:
import pandas as pd
import tensorflow as tf
from sklearn.model_selection import train_test_split
import time
import numpy as np
from scipy.stats import wilcoxon
from scipy.stats import ranksums
from sklearn.preprocessing import LabelEncoder
from keras.utils.np_utils import to_categorical
import argparse
import os
import math
import torchvision.transforms as transforms
from torchvision.utils import save_image
from torch.utils.data import DataLoader
from torchvision import datasets
from torch.autograd import Variable
import torch.nn as nn
import torch.nn.functional as F
import torch
import torch.utils.data as Data
import pandas as pd
import argparse
from tqdm.notebook import tqdm
import torchvision.transforms as transforms
from torchvision.utils import save_image
from sklearn.model_selection import StratifiedKFold
import torch.utils.data as Data
from sklearn.model_selection import train_test_split
from tensorboardX import SummaryWriter
import torch.backends.cudnn as cudnn
import random
from sklearn.metrics import roc_curve, auc, accuracy_score, precision_score, recall_score, f1_score, roc_auc_score, \
    confusion_matrix
from imblearn.combine import SMOTEENN
from sklearn.preprocessing import label_binarize
print(tf.__version__)

2.7.1


In [2]:
class Intalization():
    def __init__(self, seed_id,class_num,batch_size,tensorboard_pth):
        self.seed_id = seed_id
        self.USE_CUDA = torch.cuda.is_available()
        self.class_num = class_num
        self.device = torch.device('cuda:1' if self.USE_CUDA else 'cpu')
        self.tensorboard_pth = tensorboard_pth
        self.BATCH_SIZE = batch_size
    def set_seed(self):
        torch.manual_seed(self.seed_id)
        torch.cuda.manual_seed_all(self.seed_id)
        torch.backends.cudnn.benchmarck = False
        torch.backends.cudnn.deterministic = True
        np.random.seed(self.seed_id)
        random.seed(self.seed_id)
        os.environ['PYTHONHASHSEED'] = str(self.seed_id)

In [3]:
init = Intalization(seed_id=24,batch_size=256,class_num=2,tensorboard_pth='/home/user/CYH/oucome/linear')

In [4]:
import os
os.environ['CUDA_VISIBLE_DEVICES'] = '0'
os.environ["CUDA_LAUNCH_BLOCKING"] = '0'

In [5]:
init.set_seed()

In [6]:
data = pd.read_csv('/home/user/CYH/data/afeter_hat.csv')
data.head(5)

Pregnancies  Glucose  BloodPressure  SkinThickness  Insulin   BMI  \
0            6    148.0           72.0             35      125  33.6   
1            1     85.0           66.0             29      125  26.6   
2            8    183.0           64.0             29      125  23.3   
3            1     89.0           66.0             23       94  28.1   
4            0    137.0           40.0             35      168  43.1   

   DiabetesPedigreeFunction  Age  Outcome  
0                     0.627   50        1  
1                     0.351   31        0  
2                     0.672   32        1  
3                     0.167   21        0  
4                     2.288   33        1

In [7]:
label = data['Outcome']
data = data.drop('Outcome',axis=1)

In [8]:
data.head()

Pregnancies  Glucose  BloodPressure  SkinThickness  Insulin   BMI  \
0            6    148.0           72.0             35      125  33.6   
1            1     85.0           66.0             29      125  26.6   
2            8    183.0           64.0             29      125  23.3   
3            1     89.0           66.0             23       94  28.1   
4            0    137.0           40.0             35      168  43.1   

   DiabetesPedigreeFunction  Age  
0                     0.627   50  
1                     0.351   31  
2                     0.672   32  
3                     0.167   21  
4                     2.288   33

In [9]:
x = data
x

Pregnancies  Glucose  BloodPressure  SkinThickness  Insulin   BMI  \
0              6    148.0           72.0             35      125  33.6   
1              1     85.0           66.0             29      125  26.6   
2              8    183.0           64.0             29      125  23.3   
3              1     89.0           66.0             23       94  28.1   
4              0    137.0           40.0             35      168  43.1   
..           ...      ...            ...            ...      ...   ...   
763           10    101.0           76.0             48      180  32.9   
764            2    122.0           70.0             27      125  36.8   
765            5    121.0           72.0             23      112  26.2   
766            1    126.0           60.0             29      125  30.1   
767            1     93.0           70.0             31      125  30.4   

     DiabetesPedigreeFunction  Age  
0                       0.627   50  
1                       0.351   31  
2                       0.672   32  
3                       0.167   21  
4                       2.288   33  
..                        ...  ...  
763                     0.171   63  
764                     0.340   27  
765                     0.245   30  
766                     0.349   47  
767                     0.315   23  

[768 rows x 8 columns]

In [10]:
x = np.array(x)
label = np.array(label)

In [11]:
smote_enn = SMOTEENN(random_state=42)
x_oversampled, y_oversampled = smote_enn.fit_resample(x,label)

In [12]:
class CustomDataset(torch.utils.data.Dataset):
    def __init__(self,x,y):
        self.x = x
        self.y = y
    def __len__(self):
        return self.x.shape[0]
    def __getitem__(self,idx):
        return torch.tensor(self.x[idx]).float(),torch.tensor(self.y[idx]).long()

In [13]:
parser = argparse.ArgumentParser()
parser.add_argument("--batch_size", type=int, default=64, help="size of the batches")
parser.add_argument("--lr", type=float, default=0.0005, help="adam: learning rate")
parser.add_argument("--b1", type=float, default=0.1, help="adam: decay of first order momentum of gradient")
parser.add_argument("--b2", type=float, default=0.2, help="adam: decay of first order momentum of gradient")
parser.add_argument("--n_cpu", type=int, default=8, help="number of cpu threads to use during batch generation")
parser.add_argument("--latent_dim", type=int, default=8, help="dimensionality of the latent space")
parser.add_argument("--num_classes",type=int, default=2, help="number of classes for dataset")
opt = parser.parse_args(args=[])


class Generator(nn.Module):
    def __init__(self):
        super(Generator, self).__init__()

        def block(in_feat, out_feat, normalize=True):
            layers = [nn.Linear(in_feat, out_feat)]
            if normalize:
                layers.append(nn.BatchNorm1d(out_feat, 0.8))
            layers.append(nn.LeakyReLU(0.2, inplace=True))
#             layers.append(nn.ReLU())
            return layers

        self.model = nn.Sequential(
            *block(opt.latent_dim, 2000, normalize=True),
            *block(2000, 4000),
            *block(4000, 6000),
            *block(6000, 8000),
            *block(8000, opt.latent_dim),
            nn.Tanh()#映射到-1，1之间
        )
    
    
    
    def forward(self, z):
        output = self.model(z)#output
        output = output.reshape(z.shape[0],-1)
        return output


class Discriminator(nn.Module):
    def __init__(self):
        super(Discriminator, self).__init__()
    
        def block(in_feat, out_feat, normalize=True):
            layers = [nn.Linear(in_feat, out_feat)]
            if normalize:
                layers.append(nn.BatchNorm1d(out_feat, 0.8))
            layers.append(nn.LeakyReLU(0.2, inplace=True))
#             layers.append(nn.ReLU())
            return layers
        
        self.model = nn.Sequential(
            *block(opt.latent_dim, 8000),
            *block(8000, 6000),
            *block(6000, 4000),
            *block(4000, 2000),
            *block(2000, 1000),
        )
        
        self.adv_layers = nn.Sequential(
            nn.Linear(1000,1),
            nn.Sigmoid()                                      
        )
        
        self.aux_layers = nn.Sequential(
            nn.Linear(1000,init.class_num + 1),
            nn.Softmax()
        )
        
    def R_select(self,feature):
        feature = feature.cpu().detach().numpy()
        feature = pd.DataFrame(feature)
        mid = int((feature.shape[1]*0.5)-1)
        random_fea = random.sample(list(range(1,feature.shape[1])),mid)
        random_fea.append(0)
        feature = feature.iloc[:,random_fea]
        return feature
    
    def forward(self, f):

        output_D = self.model(f.reshape(f.shape[0],-1))
        validity = self.adv_layers(output_D)
        label = self.aux_layers(output_D)
        
        return validity,label

# Loss function for WGAN
def wasserstein_loss(real_imgs, fake_imgs):
    return torch.mean(real_imgs) - torch.mean(fake_imgs)
    
# Loss function
adversarial_loss = torch.nn.BCELoss()
auxiliary_loss = torch.nn.CrossEntropyLoss()


adversarial_loss.to(init.device)
auxiliary_loss.to(init.device)


FloatTensor = torch.cuda.FloatTensor 
LongTensor = torch.cuda.LongTensor 

In [14]:
class Trainer():
    def __init__(self,epochs,x,y):
        self.x = x
        self.y = y
        self.epochs = epochs
        self.len_train = None
        self.len_eval = None
        self.best_evalscroe = 0
        self.kfold = 10
        self.k = 0
        self.max_acc = []
        self.num_acc = []
        self.predict = []
        self.classes = []
        self.precision_score = []
        self.recall_score = []
        self.f1_score = []
        self.sepcificity_score = []
        self.auc_score = []
        
    def ten_fold_val(self):
        skf = StratifiedKFold(n_splits=self.kfold,random_state=1,shuffle=True)
        skf.get_n_splits(self.x,self.y)
        all_predict = []
        all_classes = []  
        for train_index,eval_index in skf.split(self.x,self.y):
            writer = SummaryWriter(init.tensorboard_pth+str(self.k))
            generator = Generator()
            discriminator = Discriminator()
            generator.to(init.device)
            discriminator.to(init.device)
            trainx,evalx = self.x[train_index],self.x[eval_index]
            trainy,evaly = self.y[train_index],self.y[eval_index]
            self.len_train = trainx.shape[0]
            self.len_eval = evalx.shape[0]
            print('len of train',self.len_train)
            print('len of eval',self.len_eval)
            train_dataset = CustomDataset(trainx,trainy)
            eval_dataset = CustomDataset(evalx,evaly)
            train_dataloader = torch.utils.data.DataLoader(train_dataset,batch_size=init.BATCH_SIZE,shuffle=True)
            eval_dataloader = torch.utils.data.DataLoader(eval_dataset,batch_size=init.BATCH_SIZE,shuffle=True)
            self.train(generator,discriminator,train_dataloader,eval_dataloader,writer)
            all_predict.extend(self.predict)
            all_classes.extend(self.classes)
            self.k += 1

        
    def train(self,G, D, train_dataloader, eval_dataloader, writer):
        # initialize the loss function and optimizer
        adversarial_loss = torch.nn.BCELoss().to(init.device)
        auxiliary_loss = torch.nn.CrossEntropyLoss().to(init.device)
        generator = G
        discriminator = D
        optimizer_G = torch.optim.Adam(generator.parameters(), lr=opt.lr)
        optimizer_D = torch.optim.Adam(discriminator.parameters(), lr=opt.lr)
        
        for epoch in range(self.epochs):
            print('Epoch:',epoch)
            train_G_loss = 0
            train_D_loss = 0
            train_correct = 0
            train_D_acc = []
            total = 0
            for i, (feat, labels) in enumerate(train_dataloader): 
                valid = Variable(FloatTensor(feat.size(0), 1).fill_(1.0), requires_grad=False).to(init.device)    # 真的我们都标记1
                fake = Variable(FloatTensor(feat.size(0), 1).fill_(0.0), requires_grad=False).to(init.device)    # 假的我们都标记0
                fake_aux_gt = Variable(LongTensor(feat.size(0)).fill_(opt.num_classes),requires_grad=False).to(init.device)

                real_feat = Variable(feat.type(FloatTensor)).to(init.device)

                labels = Variable(labels.type(LongTensor)).to(init.device)

                # -----------------train generator-----------------------------------
                optimizer_G.zero_grad()
                z = Variable(torch.Tensor(np.random.normal(0, 1, (feat.shape[0], opt.latent_dim)))).to(init.device)#32*4834
                gen_feat = generator(z)
                validity,_ = discriminator(gen_feat)

                g_loss = adversarial_loss(validity, valid)
                train_G_loss += g_loss


                # -----------------train discriminator--------------------------------
                optimizer_D.zero_grad()
                #loss for real feat
                real_pred,real_aux = discriminator(real_feat)
                d_real_loss = (adversarial_loss(real_pred,valid) + auxiliary_loss(real_aux,labels)) / 2

                # loss for fake feat
                fake_pred,fake_aux = discriminator(gen_feat.detach())
                d_fake_loss = (adversarial_loss(fake_pred,fake) + auxiliary_loss(fake_aux,fake_aux_gt)) / 2
                # total discriminator loss
                d_loss = (d_real_loss + d_fake_loss) / 2
                train_D_loss += d_loss
#                 D_loss.append(d_loss.item())

                # caculate discriminator accuracy
                pred = np.concatenate([real_aux.data.cpu().numpy(),fake_aux.data.cpu().numpy()],axis=0)
                gt = np.concatenate([labels.data.cpu().numpy(),fake_aux_gt.data.cpu().numpy()],axis=0)
                d_acc = np.mean(np.argmax(pred,axis=1)==gt)
            
                
                train_correct += (pred.argmax(axis=1)==gt).sum()
                train_D_acc.append(d_acc.item())
                

                d_loss.backward()
                optimizer_D.step()
#                 print(
#             "[Epoch %d/%d] [Batch %d/%d] [D loss: %f,acc: %d%%] [G loss: %f]"
#             % (epoch, opt.n_epochs, i, len(train_dataloader), d_loss.item(), 100*d_acc ,g_loss.item()))
            cur_acc = train_correct.item()/(self.len_train*2)

            writer.add_scalar('G_loss/train_G_loss',train_G_loss,global_step=epoch)
            writer.add_scalar('D_loss/train_D_loss',train_D_loss,global_step=epoch)
            writer.add_scalar('Acc/train_D_acc',cur_acc,global_step=epoch)
            print("train acc is {},train_G_loss is {}, train_D_loss is {}".format(cur_acc,train_G_loss,train_D_loss))
            self.predict,self.classes = self.evaluate(generator,discriminator, eval_dataloader,writer,epoch)

                
    def evaluate(self,G,D, eval_dataloader, writer,epoch):
        adversarial_loss = torch.nn.BCELoss().to(init.device)
        auxiliary_loss = torch.nn.CrossEntropyLoss().to(init.device)
        eval_maxacc = 0
        Max_acc = []
        predict = []
        classes = []
        pred_list = []
        y_ture = []
        generator = G#Generator().to(init.device)
        discriminator = D #Discriminator().to(init.device)
        
        with torch.no_grad():
            Gen_loss = 0
            Dis_loss = 0
            Dis_correct = 0
            
            for i, (feat, labels) in enumerate(eval_dataloader):
                # 真的我们都标记1
                valid = Variable(FloatTensor(feat.size(0), 1).fill_(1.0), requires_grad=False).to(init.device)  
                # 假的我们都标记0
                fake = Variable(FloatTensor(feat.size(0), 1).fill_(0.0), requires_grad=False).to(init.device)  
                fake_aux_gt = Variable(LongTensor(feat.size(0)).fill_(opt.num_classes),requires_grad=False).to(init.device)

                real_feat = Variable(feat.type(FloatTensor)).to(init.device)
                labels = Variable(labels.type(LongTensor)).to(init.device)

                z = Variable(torch.Tensor(np.random.normal(0, 1, (feat.shape[0], opt.latent_dim)))).to(init.device)#32*4834
                gen_feat = generator(z)
                validity,_ = discriminator(gen_feat)
                g_loss = adversarial_loss(validity, valid)
                Gen_loss += g_loss

                # ---------------train discriminator-----------------
                #loss for real feat
                real_pred,real_aux = discriminator(real_feat)
                d_real_loss = (adversarial_loss(real_pred,valid) + auxiliary_loss(real_aux,labels)) / 2

                # loss for fake feat
                fake_pred,fake_aux = discriminator(gen_feat.detach())
                d_fake_loss = (adversarial_loss(fake_pred,fake) + auxiliary_loss(fake_aux,fake_aux_gt)) / 2
                # total discriminator loss
                d_loss = (d_real_loss + d_fake_loss) / 2
                Dis_loss += d_loss

                # caculate discriminator accuracy
                pred = np.concatenate([real_aux.data.cpu().numpy(),fake_aux.data.cpu().numpy()],axis=0)
                # no geneator data
                y_pred = real_aux.data.cpu().numpy()
#                 print('pred',np.argmax(pred,axis=1))
                p = np.argmax(pred,axis=1)
                gt = np.concatenate([labels.data.cpu().numpy(),fake_aux_gt.data.cpu().numpy()],axis=0)
                # no geneator data
                y_real = labels.data.cpu().numpy()
#                 print('y_real',y_real)
                d_acc = np.mean(np.argmax(pred,axis=1)==gt)
                Dis_correct += (np.argmax(pred,axis=1)==gt).sum()
                pred_list.extend(np.argmax(pred,axis=1))
                y_ture.extend(gt)
                
                
            cur_acc = Dis_correct / (self.len_eval*2)
            print('y_true',y_ture)
            print('y_predict', pred_list)
            y_true = np.array(y_ture)
            y_pred = np.array(pred_list)
            precision = precision_score(y_true, y_pred,average='micro')
            recall = recall_score(y_true, y_pred,average='micro')
            f1 = f1_score(y_true, y_pred,average='micro')

            num_classes = len(np.unique(y_true))
            y_true_bin = label_binarize(y_true, classes=np.arange(num_classes))
            y_pred_bin = label_binarize(y_pred, classes=np.arange(num_classes))
            auc_score = []
            for i in range (opt.num_classes):
                auc = roc_auc_score(y_true_bin[:,i],y_pred_bin[:,i])
                auc_score.append(auc)
            self.precision_score.append(precision)
            self.recall_score.append(recall)
            self.f1_score.append(f1)
            self.auc_score.append(auc)
            if cur_acc > eval_maxacc:
                eval_maxacc = cur_acc
                self.num_acc.append(cur_acc)
                Max_acc = ((np.argmax(pred,axis=1)==gt))
            writer.add_scalar('G_loss/eval_G_loss',Gen_loss,global_step=epoch)
            writer.add_scalar('D_loss/eval_D_loss',Dis_loss,global_step=epoch)
            writer.add_scalar('Acc/eval_acc',cur_acc,global_step=epoch)

            print("Eval acc is {},Eval_G_loss is {}, Eval_D_loss is {}".format(cur_acc,Gen_loss,Dis_loss))
            if cur_acc > self.best_evalscroe:
                self.best_evalscroe = cur_acc
                print("best evalscore:",self.best_evalscroe)
            self.max_acc.extend(Max_acc)
            return p,gt
    def pred(self):
        pass

In [15]:
trainer = Trainer(500,x_oversampled,y_oversampled)

In [16]:
trainer.ten_fold_val()

len of train 508
len of eval 57
Epoch: 0


/home/user/anaconda3/envs/zhangfan/lib/python3.7/site-packages/torch/nn/modules/container.py:141: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.
  input = module(input)
/home/user/anaconda3/envs/zhangfan/lib/python3.7/site-packages/torch/nn/modules/container.py:141: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.
  input = module(input)


train acc is 0.7549212598425197,train_G_loss is 1.405148983001709, train_D_loss is 1.75686514377594
y_true [1, 1, 1, 0, 1, 0, 0, 0, 1, 0, 0, 1, 0, 1, 1, 0, 1, 0, 1, 0, 0, 1, 0, 1, 0, 1, 1, 1, 1, 1, 1, 0, 1, 0, 1, 0, 1, 1, 0, 0, 1, 0, 1, 0, 0, 1, 0, 1, 0, 1, 0, 1, 1, 0, 1, 1, 1, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2]
y_predict [1, 0, 1, 0, 1, 0, 0, 0, 1, 0, 0, 1, 0, 1, 1, 0, 0, 0, 0, 1, 0, 1, 0, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 0, 1, 0, 1, 1, 0, 0, 1, 0, 0, 0, 0, 1, 0, 1, 0, 1, 0, 1, 1, 0, 0, 1, 1, 0, 2, 0, 0, 2, 0, 2, 0, 0, 0, 0, 0, 2, 1, 0, 2, 2, 1, 0, 0, 1, 0, 0, 2, 0, 0, 0, 0, 1, 2, 0, 0, 2, 2, 2, 1, 0, 2, 0, 0, 0, 0, 2, 1, 2, 2, 1, 0, 1, 2, 2, 0, 1, 0, 2, 1, 0]
Eval acc is 0.5964912280701754,Eval_G_loss is 0.6927996277809143, Eval_D_loss is 0.7379209399223328
best evalscore: 0.5964912280701754
Epoch: 1
train acc is 0.5521653543307087,train_G_loss is 1.359

/home/user/anaconda3/envs/zhangfan/lib/python3.7/site-packages/torch/nn/modules/container.py:141: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.
  input = module(input)
/home/user/anaconda3/envs/zhangfan/lib/python3.7/site-packages/torch/nn/modules/container.py:141: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.
  input = module(input)


train acc is 0.4507874015748031,train_G_loss is 1.2306584119796753, train_D_loss is 1.3756498098373413
y_true [1, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 0, 1, 1, 1, 1, 1, 1, 0, 0, 1, 1, 1, 0, 0, 1, 1, 1, 1, 0, 0, 1, 0, 0, 0, 1, 1, 0, 1, 0, 0, 1, 0, 0, 1, 0, 0, 0, 0, 0, 1, 0, 1, 1, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2]
y_predict [1, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 0, 1, 1, 1, 1, 1, 1, 0, 0, 1, 1, 1, 0, 0, 1, 1, 1, 1, 1, 0, 1, 0, 0, 0, 1, 1, 0, 1, 0, 0, 1, 0, 0, 1, 0, 0, 0, 0, 1, 1, 0, 1, 0, 1, 1, 1, 0, 1, 1, 1, 0, 1, 1, 0, 1, 1, 1, 1, 0, 1, 0, 1, 0, 1, 0, 1, 0, 0, 1, 0, 0, 1, 0, 0, 1, 0, 1, 1, 1, 0, 0, 1, 1, 1, 0, 1, 0, 1, 1, 1, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0]
Eval acc is 0.47368421052631576,Eval_G_loss is 0.5881388783454895, Eval_D_loss is 0.6688032150268555
Epoch: 3
train acc is 0.453740157480315,train_G_loss is 1.1931638717651367, train_D_loss is 1

...

train acc is 0.981335952848723,train_G_loss is 13.759223937988281, train_D_loss is 0.5713292956352234
y_true [0, 1, 1, 0, 0, 1, 0, 0, 0, 1, 0, 1, 1, 1, 0, 0, 1, 0, 0, 1, 1, 1, 1, 0, 0, 1, 0, 1, 0, 1, 0, 1, 0, 1, 1, 1, 0, 0, 1, 1, 1, 1, 1, 1, 0, 1, 0, 1, 1, 1, 1, 1, 0, 1, 0, 0, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2]
y_predict [0, 1, 1, 0, 0, 1, 0, 0, 0, 1, 0, 1, 1, 1, 0, 1, 1, 0, 0, 1, 1, 1, 1, 0, 1, 1, 0, 1, 0, 1, 1, 0, 0, 1, 1, 1, 1, 0, 1, 1, 1, 1, 1, 1, 0, 1, 0, 1, 1, 1, 1, 1, 1, 1, 0, 0, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2]
Eval acc is 0.9464285714285714,Eval_G_loss is 6.9478349685668945, Eval_D_loss is 0.3007243275642395
Epoch: 495
train acc is 0.9803536345776032,train_G_loss is 13.74801254272461, train_D_loss is 0.57203191518

/home/user/anaconda3/envs/zhangfan/lib/python3.7/site-packages/torch/nn/modules/container.py:141: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.
  input = module(input)
/home/user/anaconda3/envs/zhangfan/lib/python3.7/site-packages/torch/nn/modules/container.py:141: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.
  input = module(input)


train acc is 0.9774066797642437,train_G_loss is 13.633810043334961, train_D_loss is 0.5755440592765808
y_true [1, 0, 0, 1, 0, 1, 1, 0, 1, 1, 1, 0, 0, 1, 0, 1, 1, 0, 0, 1, 1, 1, 1, 1, 0, 0, 1, 0, 0, 1, 1, 0, 1, 0, 0, 1, 1, 1, 0, 1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 0, 1, 0, 0, 0, 0, 0, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2]
y_predict [1, 0, 0, 1, 0, 1, 1, 0, 1, 1, 1, 0, 0, 1, 0, 1, 1, 0, 0, 1, 1, 1, 1, 1, 0, 1, 1, 0, 0, 1, 1, 1, 1, 0, 0, 1, 1, 0, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 0, 1, 0, 0, 0, 1, 0, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2]
Eval acc is 0.9553571428571429,Eval_G_loss is 6.640686511993408, Eval_D_loss is 0.29840999841690063
Epoch: 497
train acc is 0.981335952848723,train_G_loss is 13.643668174743652, train_D_loss is 0.5712953209

/home/user/anaconda3/envs/zhangfan/lib/python3.7/site-packages/torch/nn/modules/container.py:141: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.
  input = module(input)
/home/user/anaconda3/envs/zhangfan/lib/python3.7/site-packages/torch/nn/modules/container.py:141: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.
  input = module(input)


train acc is 0.981335952848723,train_G_loss is 13.736310958862305, train_D_loss is 0.57122802734375
y_true [0, 1, 0, 0, 1, 0, 1, 1, 0, 0, 0, 1, 1, 0, 0, 0, 1, 1, 1, 1, 1, 1, 0, 0, 0, 1, 1, 0, 1, 0, 1, 1, 1, 1, 0, 1, 1, 0, 1, 0, 1, 0, 0, 1, 1, 0, 1, 0, 0, 1, 1, 1, 1, 1, 0, 1, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2]
y_predict [0, 1, 0, 0, 1, 1, 1, 1, 0, 0, 0, 1, 1, 0, 0, 0, 1, 1, 1, 1, 1, 1, 0, 0, 0, 1, 1, 0, 1, 0, 1, 1, 0, 1, 0, 1, 1, 0, 1, 0, 1, 0, 0, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1, 1, 0, 1, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2]
Eval acc is 0.9642857142857143,Eval_G_loss is 7.030332088470459, Eval_D_loss is 0.29454243183135986
Epoch: 499
train acc is 0.981335952848723,train_G_loss is 13.832680702209473, train_D_loss is 0.5713613033294